In [1]:
import numpy as np
import os, shutil
import pandas as pd

%config Completer.use_jedi = False

In [9]:
pd.set_option('display.max_columns', 30)
pd.set_option("display.max_rows", 15000)

## Creation of Features Matrix and Target

In [205]:
df = pd.read_csv('train_ready_eff_2_6.gz')
df.shape

(5318, 12511)

In [206]:
percent_missing = df.isnull().sum()*100 / len(df)
missing_df = pd.DataFrame({'column_name': df.columns, 'percent_miss': percent_missing})

In [207]:
missing_df.sort_values(by='percent_miss', ascending=False)

column_name  \
creatinine__query_similarity_count__query_None_...  creatinine__query_similarity_count__query_None...   
potassium__query_similarity_count__query_None__...  potassium__query_similarity_count__query_None_...   
caphos_product__query_similarity_count__query_N...  caphos_product__query_similarity_count__query_...   
calcium__query_similarity_count__query_None__th...  calcium__query_similarity_count__query_None__t...   
haemoglobin__query_similarity_count__query_None...  haemoglobin__query_similarity_count__query_Non...   
ureacreat_ratio__query_similarity_count__query_...  ureacreat_ratio__query_similarity_count__query...   
glucose__query_similarity_count__query_None__th...  glucose__query_similarity_count__query_None__t...   
urea__query_similarity_count__query_None__thres...  urea__query_similarity_count__query_None__thre...   
chloride__query_similarity_count__query_None__t...  chloride__query_similarity_count__query_None__...   
albumin__query_similarity_count__query_None__th...  albumin__query_similarity_count__query_None__t...   
phosphate__query_similarity_count__query_None__...  phosphate__query_similarity_count__query_None_...   
platelet__query_similarity_count__query_None__t...  platelet__query_similarity_count__query_None__...   
alkphos__query_similarity_count__query_None__th...  alkphos__query_similarity_count__query_None__t...   
egfr__query_similarity_count__query_None__thres...  egfr__query_similarity_count__query_None__thre...   
sodium__query_similarity_count__query_None__thr...  sodium__query_similarity_count__query_None__th...   
wcc__query_similarity_count__query_None__thresh...  wcc__query_similarity_count__query_None__thres...   
haemoglobin__fft_coefficient__attr_""angle""__c...  haemoglobin__fft_coefficient__attr_""angle""__...   
alkphos__fft_coefficient__attr_""abs""__coeff_81     alkphos__fft_coefficient__attr_""abs""__coeff_81   
alkphos__fft_coefficient__attr_""imag""__coeff_95   alkphos__fft_coefficient__attr_""imag""__coeff_95   
alkphos__fft_coefficient__attr_""abs""__coeff_80     alkphos__fft_coefficient__attr_""abs""__coeff_80   
haemoglobin__fft_coefficient__attr_""angle""__c...  haemoglobin__fft_coefficient__attr_""angle""__...   
haemoglobin__fft_coefficient__attr_""angle""__c...  haemoglobin__fft_coefficient__attr_""angle""__...   
haemoglobin__fft_coefficient__attr_""angle""__c...  haemoglobin__fft_coefficient__attr_""angle""__...   
alkphos__fft_coefficient__attr_""imag""__coeff_96   alkphos__fft_coefficient__attr_""imag""__coeff_96   
alkphos__fft_coefficient__attr_""imag""__coeff_97   alkphos__fft_coefficient__attr_""imag""__coeff_97   
alkphos__fft_coefficient__attr_""imag""__coeff_98   alkphos__fft_coefficient__attr_""imag""__coeff_98   
haemoglobin__fft_coefficient__attr_""angle""__c...  haemoglobin__fft_coefficient__attr_""angle""__...   
alkphos__fft_coefficient__attr_""abs""__coeff_73     alkphos__fft_coefficient__attr_""abs""__coeff_73   
haemoglobin__fft_coefficient__attr_""angle""__c...  haemoglobin__fft_coefficient__attr_""angle""__...   
alkphos__fft_coefficient__attr_""abs""__coeff_79     alkphos__fft_coefficient__attr_""abs""__coeff_79   
caphos_product__fft_coefficient__attr_""real""_...  caphos_product__fft_coefficient__attr_""real""...   
alkphos__fft_coefficient__attr_""abs""__coeff_78     alkphos__fft_coefficient__attr_""abs""__coeff_78   
alkphos__fft_coefficient__attr_""imag""__coeff_99   alkphos__fft_coefficient__attr_""imag""__coeff_99   
albumin__fft_coefficient__attr_""imag""__coeff_99   albumin__fft_coefficient__attr_""imag""__coeff_99   
alkphos__fft_coefficient__attr_""abs""__coeff_77     alkphos__fft_coefficient__attr_""abs""__coeff_77   
alkphos__fft_coefficient__attr_""abs""__coeff_76     alkphos__fft_coefficient__attr_""abs""__coeff_76   
alkphos__fft_coefficient__attr_""abs""__coeff_75     alkphos__fft_coefficient__attr_""abs""__coeff_75   
alkphos__fft_coefficient__attr_""abs""__coeff_74     alkphos__fft_coefficient__attr_""abs""__coeff_7

In [208]:
df['eskd_intraining'].value_counts()

non_eskd    4687
eskd         631
Name: eskd_intraining, dtype: int64

In [209]:
df.query("eskd_intraining != 'eskd'", inplace=True)
df.shape

(4687, 12511)

In [210]:
df.set_index('id', inplace=True)

In [211]:
def drop_missing(df):
    col_missing_thresh_col = len(df)*0.7
#     row_missing_thresh_col = len(df.columns)*0.3
    df.dropna(axis=1, thresh=col_missing_thresh_col, inplace=True)
#     df.dropna(axis=0, thresh=row_missing_thresh_col, inplace=True)
    
    return df

def to_category(df):
    cols = df.select_dtypes(include='object').columns
    for col in cols:
        df[col] = df[col].astype('category')
    return df

def copy_df(df):
    return df.copy()

In [212]:
df_cleaned = (df.pipe(copy_df).pipe(drop_missing).pipe(to_category))
df_cleaned.shape

(4687, 3841)

In [213]:
percent_missing = df_cleaned.isnull().sum()*100 / len(df)
missing_df_cleaned = pd.DataFrame({'column_name': df_cleaned.columns, 'percent_miss': percent_missing})
missing_df_cleaned.sort_values(by='percent_miss', ascending=False)

column_name  \
wcc__autocorrelation__lag_2                                               wcc__autocorrelation__lag_2   
wcc__cwt_coefficients__coeff_2__w_5__widths_(2,...  wcc__cwt_coefficients__coeff_2__w_5__widths_(2...   
wcc__cwt_coefficients__coeff_2__w_2__widths_(2,...  wcc__cwt_coefficients__coeff_2__w_2__widths_(2...   
wcc__cwt_coefficients__coeff_2__w_20__widths_(2...  wcc__cwt_coefficients__coeff_2__w_20__widths_(...   
wcc__mean_second_derivative_central                               wcc__mean_second_derivative_central   
wcc__skewness                                                                           wcc__skewness   
wcc__cwt_coefficients__coeff_2__w_10__widths_(2...  wcc__cwt_coefficients__coeff_2__w_10__widths_(...   
wcc__permutation_entropy__dimension_3__tau_1             wcc__permutation_entropy__dimension_3__tau_1   
chloride__cwt_coefficients__coeff_2__w_5__width...  chloride__cwt_coefficients__coeff_2__w_5__widt...   
chloride__cwt_coefficients__coeff_2__w_10__widt...  chloride__cwt_coefficients__coeff_2__w_10__wid...   
chloride__cwt_coefficients__coeff_2__w_20__widt...  chloride__cwt_coefficients__coeff_2__w_20__wid...   
chloride__skewness                                                                 chloride__skewness   
chloride__permutation_entropy__dimension_3__tau_1   chloride__permutation_entropy__dimension_3__tau_1   
chloride__mean_second_derivative_central                     chloride__mean_second_derivative_central   
chloride__cwt_coefficients__coeff_2__w_2__width...  chloride__cwt_coefficients__coeff_2__w_2__widt...   
haemoglobin__skewness                                                           haemoglobin__skewness   
haemoglobin__mean_second_derivative_central               haemoglobin__mean_second_derivative_central   
haemoglobin__cwt_coefficients__coeff_2__w_20__w...  haemoglobin__cwt_coefficients__coeff_2__w_20__...   
haemoglobin__cwt_coefficients__coeff_2__w_5__wi...  haemoglobin__cwt_coefficients__coeff_2__w_5__w...   
haemoglobin__cwt_coefficients__coeff_2__w_10__w...  haemoglobin__cwt_coefficients__coeff_2__w_10__...   
haemoglobin__cwt_coefficients__coeff_2__w_2__wi...  haemoglobin__cwt_coefficients__coeff_2__w_2__w...   
haemoglobin__permutation_entropy__dimension_3__...  haemoglobin__permutation_entropy__dimension_3_...   
haemoglobin__autocorrelation__lag_2                               haemoglobin__autocorrelation__lag_2   
albumin__autocorrelation__lag_2                                       albumin__autocorrelation__lag_2   
phosphate__autocorrelation__lag_0                                   phosphate__autocorrelation__lag_0   
phosphate__autocorrelation__lag_1                                   phosphate__autocorrelation__lag_1   
phosphate__fourier_entropy__bins_100                             phosphate__fourier_entropy__bins_100   
phosphate__fourier_entropy__bins_5                                 phosphate__fourier_entropy__bins_5   
phosphate__fourier_entropy__bins_3                                 phosphate__fourier_entropy__bins_3   
phosphate__fourier_entropy__bins_10                               phosphate__fourier_entropy__bins_10   
phosphate__fourier_entropy__bins_2                                 phosphate__fourier_entropy__bins_2   
caphos_product__linear_trend__attr_""slope""             caphos_product__linear_trend__attr_""slope""   
caphos_product__fft_coefficient__attr_""angle""...  caphos_product__fft_coefficient__attr_""angle"...   
caphos_product__mean_abs_change                                       caphos_product__mean_abs_change   
caphos_product__linear_trend__attr_""pvalue""           caphos_product__linear_trend__attr_""pvalue""   
caphos_product__linear_trend__attr_""intercept""     caphos_product__linear_trend__attr_""intercept""   
caphos_product__fft_coefficient__attr_""imag""_...  caphos_product__fft_coefficient__attr_""imag""...   
caphos_product__mean_change                                               caphos_product__mean_chang

In [214]:
df_cleaned['eskd_2y'].value_counts()

non_eskd    4589
eskd          98
Name: eskd_2y, dtype: int64

In [215]:
df_cleaned['eskd_5y'].value_counts()

non_eskd    4466
eskd         221
Name: eskd_5y, dtype: int64

In [216]:
imbalance_ratio = df_cleaned['eskd_5y'].value_counts().non_eskd / df_cleaned['eskd_5y'].value_counts().eskd
imbalance_ratio

20.20814479638009

In [217]:
df_cleaned_numeric = df_cleaned.select_dtypes(include=['int', 'float'])
inf_cols_name = list(df_cleaned_numeric.columns.to_series()[np.isinf(df_cleaned_numeric).any()])

In [218]:
df_cleaned.drop(inf_cols_name, axis=1, inplace=True)

In [219]:
X = df_cleaned.drop(['egfr.y', 'eskd_intraining', 'eskd_2y', 'eskd_5y'], axis=1)
y = df_cleaned['eskd_5y'].values

In [220]:
y = y.map({'non_eskd':'no', 'eskd': 'yes'})

In [221]:
y

['no', 'no', 'no', 'no', 'no', ..., 'no', 'no', 'no', 'no', 'no']
Length: 4687
Categories (2, object): ['yes', 'no']

In [222]:
from sklearn.preprocessing import OneHotEncoder
from sklearn.compose import ColumnTransformer
category_cols = list(X.select_dtypes(include='category').columns)
one_hot = OneHotEncoder()
transformer = ColumnTransformer([('one_hot', one_hot, category_cols)],remainder='passthrough')
X_transformed = transformer.fit_transform(X)

In [223]:
from sklearn.preprocessing import LabelEncoder
lab_encode = LabelEncoder()

In [224]:
y_transformed = lab_encode.fit_transform(y)

In [225]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X_transformed, y_transformed, stratify=y_transformed,
                                                   test_size=0.3, random_state=7)

In [226]:
import xgboost as xgb
xgb_class = xgb.XGBClassifier(n_jobs=-1, random_state = 7, n_estimators=1000, scale_pos_weight=imbalance_ratio,
                             use_label_encoder=False)
xgb_class

XGBClassifier(base_score=None, booster=None, colsample_bylevel=None,
              colsample_bynode=None, colsample_bytree=None, gamma=None,
              gpu_id=None, importance_type='gain', interaction_constraints=None,
              learning_rate=None, max_delta_step=None, max_depth=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=1000, n_jobs=-1, num_parallel_tree=None,
              random_state=7, reg_alpha=None, reg_lambda=None,
              scale_pos_weight=20.20814479638009, subsample=None,
              tree_method=None, use_label_encoder=False,
              validate_parameters=None, verbosity=None)

In [227]:
xgb_class.fit(X=X_train, y=y_train, eval_metric='error')

XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
              colsample_bynode=1, colsample_bytree=1, gamma=0, gpu_id=-1,
              importance_type='gain', interaction_constraints='',
              learning_rate=0.300000012, max_delta_step=0, max_depth=6,
              min_child_weight=1, missing=nan, monotone_constraints='()',
              n_estimators=1000, n_jobs=-1, num_parallel_tree=1, random_state=7,
              reg_alpha=0, reg_lambda=1, scale_pos_weight=20.20814479638009,
              subsample=1, tree_method='exact', use_label_encoder=False,
              validate_parameters=1, verbosity=None)

In [228]:
y_pred = xgb_class.predict(X_test)

In [229]:
from sklearn.metrics import roc_auc_score, classification_report, matthews_corrcoef, confusion_matrix

In [230]:
confusion_matrix(y_test, y_pred)

array([[1325,   16],
       [  55,   11]])

In [231]:
matthews_corrcoef(y_test, y_pred)

0.23848125836155976

In [232]:
params = {'n_estimators':[100, 250, 500, 750, 1000],
          'max_depth':[1, 5, 7, 10, 15, 20, 50, 100] ,
          'learning_rate':[0.001, 0.01, 0.1, 1, 10],
          'subsample':[0.3, 0.5, 0.7, 0.9],
          'colsample_bytree':[0.3, 0.5, 0.7, 0.9],
          'scale_pos_weight':[10, 20, 30, 40],
}

In [233]:
from sklearn.model_selection import StratifiedKFold, GridSearchCV

In [235]:
cv_method = StratifiedKFold(n_splits=5)

In [237]:
model_xgb = GridSearchCV(estimator=xgb_class, cv= cv_method, param_grid=params)

In [ ]:
model_xgb.fit(X_train, y_train)

[07:09:56] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:09:57] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:09:59] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:10:00] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

[07:10:46] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:10:48] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:10:49] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:10:51] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

[07:11:37] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:11:38] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:11:40] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:11:41] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

[07:13:03] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:13:07] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:13:10] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:13:13] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

[07:14:58] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:15:01] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:15:05] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[07:15:08] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

...

[08:09:55] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:10:03] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:10:12] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:10:20] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

[08:17:29] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:17:44] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:18:00] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:18:15] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

[08:26:22] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:40] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:26:58] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:27:09] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

[08:36:03] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:36:29] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:36:56] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:37:22] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

[08:49:08] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:25] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:49:48] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[08:50:11] WARNING: ../src/learner.cc:1095: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old be

In [ ]:
model_xgb.best_params_

In [29]:
y_pred = model_xgb.predict(X_test)
y_pred

array([0, 0, 0, ..., 0, 0, 0])

In [32]:
conf_matrix = confusion_matrix(y_test, y_pred)
conf_matrix

array([[1233,    2],
       [  36,    1]])

In [33]:
mcc = matthews_corrcoef(y_test,y_pred=y_pred)
mcc

0.08802508244377058

### SMAC Hyperparameter Tuning